2.0.1) Preprocessing the fees column

In [ ]:
import pandas as pd
import requests
import regex as re
from tqdm import tqdm

In [21]:
file_path = "merged_tsv.tsv"
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)
data = pd.read_csv(file_path, sep='\t')
sample_data = data.head(10)
sample_data
df= pd.read_csv("merged_tsv.tsv", sep = '\t')

This function is used to manage numbers in which there is a point inside. There are 3 possible cases that after the point there are 1 2 or 3 numbers, when there are 2 numbers or 1 it returns the integer part. When there are 3 numbers it removes the dot and rewrites the number without it. 

In [22]:
def custom_float_conversion(text):
    # Utilizza una regular expression per trovare numeri con al massimo 3 cifre decimali
    pattern = r'(\d+)\.(\d{1,3})\b'
    result = re.sub(pattern, lambda match: match.group(1) + match.group(2).ljust(3, '0') if len(match.group(2)) == 3 else match.group(1), text)
    
    return result


In [23]:
df['fees'] = df['fees'].astype(str).apply(custom_float_conversion)
df['fees']

0                                                                                                                                                                                                                                                                                                Tuition fee per year (non-EU/EEA students): 15000 €
1                                                                                                                                                                                                                                                                                                                                                nan
2                                                                                                                                                                                                                                                               For EU nationals: 155 Euro per semester For non-EU nationals: 

This function with the help of an API converts all other currencies into EURO

In [24]:
import requests

def convert_to_euro(valore, simbolo):
    
    if simbolo.upper() == 'EUR':
        return valore
    
    api_key = "3d76141f0728a99e7ed28ef8e2c010c0"
    
    # CurrencyLayer uses 'source' for base currency and a list of 'currencies' for conversion
    url = f"http://apilayer.net/api/live?access_key={api_key}&source={simbolo}&currencies=EUR&format=1"
    
    response = requests.get(url)
    if response.status_code == 200:
        data = response.json()

        if data.get('success', False):
            rates = data.get('quotes', {})
            conversion_key = f"{simbolo}EUR"
            
            if conversion_key in rates:
                euro_rate = rates[conversion_key]
                return valore * euro_rate
            else:
                print(f"Conversion rate not found for: {conversion_key}")  # Debugging print
        else:
            print(f"API Error: {data.get('error')}")  # Debugging print
    else:
        print(f"Failed to fetch rates. Status code: {response.status_code}")  # Debugging print

    return None


This function searches for currency symbols or names and searches for the value checking whether it is before or after the currency symbol or name calculates the maximum and uses the convert_to_euro function to convert this value to the respective value in euro 

In [31]:
import regex as re

currency_mapping = {
    '€': 'EUR',
    '$': 'USD',
    '£': 'GBP',
    'Euro': 'EUR',
    'euro': 'EUR',
    'Pound': 'GBP',
    'Euros': 'EUR',
    'HK$': 'HKD',
    'GBP£': 'GBP',
    'HKD$': 'HKD',
    
    
    
    # Add more mappings as needed
}

def trova_simboli_e_valori(testo):
    
    if not isinstance(testo, str):
        return testo
    
    pattern = re.compile(r'(\p{Sc}|Euro|Dollar|Pound|Euros|SEK|EUR|HK$|USD|JPY|HKD|CHF|HKD$|RMB|CZK|YEN|ISK|HKD|GBP|GBP£)?(\d+(?:,\d{3})*(?:\.\d{1,2})?)(?(1)|\s*(\p{Sc}|Euro|Dollar|Pound|Euros|SEK|EUR|HK$|USD|JPY|HKD|CHF|HKD$|RMB|CZK|YEN|ISK|HKD|GBP|GBP£))', re.IGNORECASE | re.UNICODE)
   
    risultati = pattern.findall(testo)

    max_val = None
    valuta = None

    if risultati:
        risultati_list = []
        for match in risultati:
            
            simbolo = currency_mapping.get(match[0], match[0]) if match[0] else currency_mapping.get(match[2], match[2])
            valore = float(match[1].replace(',', ''))
            risultati_list.append(valore)


        # Find the maximum value in Euros
        max_val = max(risultati_list)
        max_val_converted = convert_to_euro(max_val, simbolo)
        return f"EUR: {max_val_converted:.0f}" if max_val_converted is not None else f"{max_val}"
        
    else:
        return testo

In [32]:
df['fees']=df['fees'].apply(trova_simboli_e_valori)
df['fees']

0                                                                                                                                                                                                                                                                                                                                            15000.0
1                                                                                                                                                                                                                                                                                                                                                nan
2                                                                                                                                                                                                                                                                                                                             